# GSM to Python Project

In [1]:
# determine the current project folder
import pathlib

# determine the current project folder
project_folder = pathlib.Path().parent.absolute()
project_folder

WindowsPath('c:/Users/Lenovo/Desktop/Malik-Burcu-LAB/GSM/GSM-to-python')

# Seeds

In [3]:
# set specific seeds to get the exact same results across different experiments
import numpy as np
import random

np.random.seed(44)
random.seed(44)

# User Input Parameters

In [4]:
INPUT_FILE_NAME = "GDS1962.csv"
GROUP_FILE_NAME = "cancer-DisGeNET.txt"
GROUP_COLUMN_NAME = "diseaseName"

NUMBER_OF_ITERATION = 5
MODEL_NAME = "RandomForest" # DecisionTree, RandomForest, SVM, KNN, MLP
LABEL_OF_POSITIVE_CLASS = "pos"
LABEL_OF_NEGATIVE_CLASS = "neg"
CLASS_MIN_BALANCE_RATIO = 0.5 # this is to handle imbalanced data by undersampling the majority class 
# (e.g. if the ratio is 0.5, the majority class has 1000 samples, and the minority class has 200 samples, then the majority class will be undersampled to 400 samples)
TRAIN_TEST_RATIO = 0.7

NORMALIZATION = "minmax" # minmax, zscore
FILTER_FEATURES_BY_TTEST_TO = 1000 # 0 to disable
FILTER_BEST_X_GROUPS = 10

# Input

In [5]:
# read the csv input from data folder
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

# read the csv input from data folder
data_folder = project_folder / "data"
data_file = data_folder / INPUT_FILE_NAME
data = pd.read_csv(data_file)

In [6]:
# print the first 5 rows of the data
data.head()

class  MIR4640   RFC2  HSPA6    PAX8  GUCA1A  MIR5193   THRA  PTPN21  CCL5  \
0   neg   4701.5  282.7  769.6  1616.3   232.7    357.7  245.1    33.2  30.7   
1   neg   4735.0  347.9  287.9  1527.2   204.8    336.5  186.2    22.9  57.1   
2   neg   2863.9  355.0  199.0  1793.8   119.3    328.7  349.3    30.0  17.8   
3   neg   5350.2  319.9  182.8  1880.0   180.2    304.7  325.4    47.6  30.7   
4   neg   4789.4  294.2  204.3  1012.0   156.7    190.1  132.0    18.8  11.8   

   ...  LRCH4(2)  LRTM1(1)  MIR1306(3)  91682_at  EXOSC4(2)  EHBP1L1(3)  \
0  ...     453.4      30.8       585.5     724.2      476.0       215.8   
1  ...     439.9      34.1       453.2     603.1      347.1       269.6   
2  ...     200.0     111.0       370.6     641.4      419.3       269.5   
3  ...     565.1      19.3       501.2     579.7      289.4       205.6   
4  ...     395.4      37.8       439.6     523.0      408.0       240.4   

   MEX3D(2)  EPS8L1(4)  BCAN(3)  DCAF15(3)  
0    1002.0       71.7   1524.7      318.9  
1    1017.2       33.0   1742.0      304.5  
2     745.8       51.0   1333.5      322.0  
3     959.7      165.1   1572.5      302.9  
4     996.8       48.7   1226.0      230.4  

[5 rows x 54614 columns]

In [7]:
# the input is like::
# class	MIR4640	PAX8	EPHB3	SPATA17	PRR22	PRR22 (#1)	SLC39A5	NEXN	MFAP3	...	FAXDC2 (#1)	SLC48A1 (#2)	DTX3 (#3)	SIGIRR (#1)	SIDT2 (#1)	HIF1AN (#2)	MIR1306 (#2)	FAM86DP	ADGRA2 (#1)	EHBP1L1 (#3)
# 0	neg	4701.5	1616.3	107.5	13.3	56.2	291.1	205.2	219.3	42.6	...	3960.7	2253.8	554.5	606.9	2954.2	495.1	422.6	441.5	336.8	215.8
# 1	neg	4735.0	1527.2	270.8	12.8	51.2	209.5	265.3	109.2	77.7	...	3799.2	2528.8	626.8	868.3	2760.5	425.5	488.2	359.7	376.4	269.6

## Missing Values

In [8]:
# get rid of missing values and measure how many rows are removed
print("Before dropping missing values: ", data.shape)
data = data.dropna()
print("After dropping missing values: ", data.shape)

Before dropping missing values:  (180, 54614)
After dropping missing values:  (179, 54614)


## Group File

In [9]:
# get group file from data / group_file / {file}
# its format is like::
# geneSymbol	diseaseName
# A1BG	Glioblastoma
# A1BG	Meningioma
# A1BG	Subependymal Giant Cell Astrocytoma

group_file = data_folder / "group_file" / GROUP_FILE_NAME
group = pd.read_csv(group_file, sep="\t")
group.tail()

geneSymbol                         diseaseName
329931   LNC-LBCS  Hormone refractory prostate cancer
329932   MIR223HG                            leukemia
329933   MIR223HG         Leukemia, Myelocytic, Acute
329934   MIR223HG                      Leukemogenesis
329935   MIR223HG                  Childhood Leukemia

### Get Unique Group Names

In [10]:
groups = group.iloc[:, 1].unique()

print("Number of groups: ", len(groups))
print("Groups: ", groups)

Number of groups:  3929
Groups:  ['Glioblastoma' 'Meningioma' 'Subependymal Giant Cell Astrocytoma' ...
 "Leukemic Phase of Non-Hodgkin's Lymphoma"
 'Thyroid Gland Follicular Carcinoma, Encapsulated Angioinvasive'
 'Thyroid Gland Follicular Carcinoma, Widely Invasive']


# ✅✅ GSM ✅✅

## Sample by the smallest class

In [11]:
# Measure the amount of samples for each class.
# Then, pick the class with the least amount of samples and reduce the other classes to the same amount.
# This is to avoid the problem of imbalanced data.

# get the number of samples for each class
print("Number of samples for each class:")
print(data["class"].value_counts())

# get the class with the least amount of samples
min_samples = data["class"].value_counts().min()
print("Minimum number of samples: ", min_samples)

# reduce the other classes to the amount of specified ratio
data = data.groupby("class").head(min_samples / CLASS_MIN_BALANCE_RATIO)
print("Number of samples for each class after reducing:")
print(data["class"].value_counts())

Number of samples for each class:
class
pos    156
neg     23
Name: count, dtype: int64
Minimum number of samples:  23
Number of samples for each class after reducing:
class
pos    46
neg    23
Name: count, dtype: int64


## Normalization

In [12]:
from sklearn.preprocessing import MinMaxScaler, StandardScaler

# apply normalization
if NORMALIZATION == "minmax":
    scaler = MinMaxScaler()
elif NORMALIZATION == "zscore":
    scaler = StandardScaler()
else:
    raise Exception("Invalid normalization method")

# get the data without the class column
data_without_class = data.drop("class", axis=1)

# normalize the data
data_normalized = scaler.fit_transform(data_without_class)

# convert the normalized data to a dataframe
data_normalized = pd.DataFrame(data_normalized, columns=data_without_class.columns)

# add the class column to the normalized data at the beginning
data_normalized.insert(0, "class", data["class"])


In [13]:
data_normalized.head(2)

class   MIR4640      RFC2     HSPA6      PAX8    GUCA1A   MIR5193      THRA  \
0   neg  0.171721  0.053382  0.198423  0.517653  0.695238  0.244529  0.384350   
1   neg  0.174484  0.113392  0.068805  0.448211  0.609524  0.213598  0.214902   

     PTPN21      CCL5  ...  LRCH4(2)  LRTM1(1)  MIR1306(3)  91682_at  \
0  0.090819  0.012672  ...  0.164024  0.268915    0.383838  0.501767   
1  0.039702  0.025202  ...  0.155285  0.298997    0.240143  0.348940   

   EXOSC4(2)  EHBP1L1(3)  MEX3D(2)  EPS8L1(4)   BCAN(3)  DCAF15(3)  
0   0.306900    0.167142  0.107994   0.340727  0.084897   0.228889  
1   0.132168    0.252376  0.112450   0.102280  0.102537   0.209117  

[2 rows x 54614 columns]

In [14]:
# change the class column to numerical
data_normalized["class"].replace({LABEL_OF_NEGATIVE_CLASS: 0, LABEL_OF_POSITIVE_CLASS: 1}, inplace=True)

## Filter Features by TTest

In [15]:
# # apply anova test to the each feature of the train data
# from scipy import stats
# from tqdm import tqdm

# def apply_anova_levene_test(data, FILTER_FEATURES_BY_TTEST_TO):
#     # Apply ANOVA test to each feature
#     anova_results = {}
    
#     for column in tqdm(data.columns[1:]):  # Skip the 'class' column
#         f_val, p_val = stats.f_oneway(data[data['class'] == 'pos'][column], data[data['class'] == 'neg'][column])
#         anova_results[column] = p_val

#     # Sort features by p-value in ascending order (lower p-value means more significant)
#     sorted_features = sorted(anova_results, key=anova_results.get)

#     # Select the top FILTER_FEATURES_BY_TTEST_TO features
#     top_features = sorted_features[:FILTER_FEATURES_BY_TTEST_TO]

#     return top_features

In [16]:
from sklearn.feature_selection import SelectKBest, chi2

selector = SelectKBest(score_func=chi2, k=FILTER_FEATURES_BY_TTEST_TO)  # Select top 2 features
X_new = selector.fit_transform(data_normalized, data_normalized["class"])

# Get the selected feature names
selected_feature_names = data_normalized.columns[selector.get_support()]

# Convert the selected features to a DataFrame
data_filtered = pd.DataFrame(data_normalized, columns=selected_feature_names)

In [17]:
# apply one-way anova
# significant_features = apply_anova_levene_test(train, FILTER_FEATURES_BY_TTEST_TO)

In [18]:
# print(f"Significant features: {significant_features}")


In [19]:
# filter the data by the features
# train_v2 = train[["class"] + significant_features]
# test_v2 = test[["class"] + significant_features]

# test_v2.shape, train_v2.shape


In [20]:
# train_v2.head(2)


In [21]:
# count how many common features does filtered_features have with significant_features (old vs new method)
# common_features = len(set(filtered_features) & set(significant_features))
# print(f"Number of common features: {common_features}")

In [22]:
# from line_profiler import LineProfiler
# lp = LineProfiler()
# # lp.run("apply_anova_levene_test(train, FILTER_FEATURES_BY_TTEST_TO)")
# lp_wrapper = lp(apply_anova_levene_test)
# lp_wrapper(train, FILTER_FEATURES_BY_TTEST_TO)

## Split Data by Train and Test

In [23]:
# split the data into train and test
from sklearn.model_selection import train_test_split

def split_data(data):
    train, test = train_test_split(data, test_size=1 - TRAIN_TEST_RATIO, stratify=data["class"])
    print("Number of training samples: ", len(train))
    print("Number of test samples: ", len(test))
    return train, test

train_v2, test_v2 = split_data(data_filtered)

Number of training samples:  48
Number of test samples:  21


## Grouping

In [24]:
# some columns are like "PRR22 (#1)" or "SLC48A1 (#2)" 
# but we need to remove the (#1) or (#2) part in order to make the column name valid while matching them with the group file
import re
def remove_parenthesis(s):
    return re.sub(r'\s*\(.*\)\s*', '', s)

In [25]:
# # get the features and find which groups they are related to using the grouping file
# # for each feature, store the groups it is related to in a dictionary.

# def get_groups_of_features(data, group):
#     # get the features from the data
#     features = data.columns[1:]
#     # create a dictionary to store the groups that are related to the features 
#     group_of_features = {}
#     # for each feature
#     for feature in features:
#         # remove the parenthesis from the feature name
#         feature_fixed = remove_parenthesis(feature)
#         # get the group of the feature
#         groups = group[group[] == feature_fixed]["diseaseName"].to_list()
#         # store the groups of the feature
#         # while storing the feature, use it with the original name such as "PRR22 (#1)"
#         group_of_features[feature] = groups
#     # return the groups of features
#     return group_of_features


In [26]:
# # get the groups of features
# groups_of_features = get_groups_of_features(train_v2, group)
# # print the groups of features
# print(f"{groups_of_features}")

In [27]:
# # print the first 6 element of groups of features
# for feature, groups in list(groups_of_features.items())[:6]:
#     print(feature, groups)

In [28]:
def get_features_of_each_group(group):
    unique_groups = group.iloc[:,1].unique()
    filters_of_unique_groups = {}
    for group_name in unique_groups:
        # get the features that are related to the group
        features_of_group = group[group.iloc[:, 1] == group_name].iloc[:, 0].to_list()

        filters_of_unique_groups[group_name] = features_of_group
    return filters_of_unique_groups

In [29]:
featureList_of_groups = get_features_of_each_group(group)

In [30]:
featureList_of_groups

{'Glioblastoma': ['A1BG',
  'NAT2',
  'SERPINA3',
  'AAVS1',
  'ABCA1',
  'ABL1',
  'ABO',
  'ACACA',
  'ACACB',
  'ACAT1',
  'ASIC2',
  'ASIC1',
  'ACP1',
  'ACP3',
  'ACTB',
  'ACTC1',
  'ACTG1',
  'ACTG2',
  'ACTN4',
  'ADA',
  'ADAM8',
  'ADAM10',
  'ADAR',
  'ADARB1',
  'ADARB2',
  'ADCYAP1',
  'ADCYAP1R1',
  'ADD3',
  'ADM',
  'PARP1',
  'ADRA1A',
  'ADRA2B',
  'GRK3',
  'AEBP1',
  'AGRP',
  'JAG1',
  'AGT',
  'APLNR',
  'AGXT',
  'AHR',
  'AHSG',
  'AIF1',
  'AKT1',
  'AKT2',
  'ALB',
  'ALCAM',
  'ALDH1A1',
  'ALDH3A1',
  'ALDH1A3',
  'AKR1B1',
  'ALK',
  'ALOX5',
  'ALPI',
  'ALPP',
  'AMELX',
  'AMFR',
  'AMH',
  'ANCR',
  'ANG',
  'ANGPT1',
  'ANGPT2',
  'ANXA1',
  'ANXA2',
  'ANXA5',
  'ANXA7',
  'APAF1',
  'APC',
  'APEX1',
  'BIRC3',
  'XIAP',
  'BIRC5',
  'APLP2',
  'APOA1',
  'APOA4',
  'APOB',
  'AQP8',
  'APOD',
  'APOE',
  'APP',
  'APRT',
  'FAS',
  'FASLG',
  'AQP1',
  'AQP4',
  'AQP9',
  'AR',
  'ARAF',
  'AREG',
  'ARF1',
  'ARF4',
  'ARG1',
  'ARG2',
  'RHOA',
 

In [31]:
# print the first 6 element of groups of features
for feature, groups in list(featureList_of_groups.items())[:6]:
    print(feature, groups)

Glioblastoma ['A1BG', 'NAT2', 'SERPINA3', 'AAVS1', 'ABCA1', 'ABL1', 'ABO', 'ACACA', 'ACACB', 'ACAT1', 'ASIC2', 'ASIC1', 'ACP1', 'ACP3', 'ACTB', 'ACTC1', 'ACTG1', 'ACTG2', 'ACTN4', 'ADA', 'ADAM8', 'ADAM10', 'ADAR', 'ADARB1', 'ADARB2', 'ADCYAP1', 'ADCYAP1R1', 'ADD3', 'ADM', 'PARP1', 'ADRA1A', 'ADRA2B', 'GRK3', 'AEBP1', 'AGRP', 'JAG1', 'AGT', 'APLNR', 'AGXT', 'AHR', 'AHSG', 'AIF1', 'AKT1', 'AKT2', 'ALB', 'ALCAM', 'ALDH1A1', 'ALDH3A1', 'ALDH1A3', 'AKR1B1', 'ALK', 'ALOX5', 'ALPI', 'ALPP', 'AMELX', 'AMFR', 'AMH', 'ANCR', 'ANG', 'ANGPT1', 'ANGPT2', 'ANXA1', 'ANXA2', 'ANXA5', 'ANXA7', 'APAF1', 'APC', 'APEX1', 'BIRC3', 'XIAP', 'BIRC5', 'APLP2', 'APOA1', 'APOA4', 'APOB', 'AQP8', 'APOD', 'APOE', 'APP', 'APRT', 'FAS', 'FASLG', 'AQP1', 'AQP4', 'AQP9', 'AR', 'ARAF', 'AREG', 'ARF1', 'ARF4', 'ARG1', 'ARG2', 'RHOA', 'RHOB', 'RHOC', 'RND3', 'ARHGAP1', 'ARNTL', 'ARR3', 'ARRB1', 'ARSA', 'STS', 'ART1', 'ASAH1', 'ASCL1', 'ASL', 'ASPA', 'ASS1', 'ATF1', 'ATF3', 'ATF4', 'ATM', 'ATP1A1', 'ATP1A3', 'ATP1B2', 'AT

##  Scoring

In [32]:
# Take each column separately
# Split it into 80:20 ratio for training and testing
# Apply the normalization method
# Train the model with the selected model
# Predict the test data
# Calculate the necessary metrics
# Repeat the process 5 times
# Calculate the average of the metrics

from sklearn.model_selection import train_test_split
from sklearn import preprocessing
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn import svm
from sklearn.neighbors import KNeighborsClassifier
from sklearn.neural_network import MLPClassifier

# split the data into train and test
def split_data(data):
    # get the features
    features = data.columns[1:]
    # get the class labels
    labels = data["class"]
    # split the data into train and test
    train_x, test_x, train_y, test_y = train_test_split(data[features], labels, test_size=0.2, random_state=42)
    # return the train and test data
    return train_x, test_x, train_y, test_y

# normalize the data
def normalize_data(train_x, test_x, NORMALIZATION):
    # normalize the data
    if NORMALIZATION == "minmax":
        # create the scaler
        scaler = preprocessing.MinMaxScaler()
    elif NORMALIZATION == "zscore":
        # create the scaler
        scaler = preprocessing.StandardScaler()
    else:
        raise Exception("Invalid normalization method")
    # fit the scaler
    scaler.fit(train_x)
    # normalize the train and test data
    train_x = scaler.transform(train_x)
    test_x = scaler.transform(test_x)
    # return the normalized train and test data
    return train_x, test_x

# train the model
def train_model(train_x, train_y, MODEL_NAME):
    # train the model
    if MODEL_NAME == "DecisionTree":
        # create the model
        model = DecisionTreeClassifier()
    elif MODEL_NAME == "RandomForest":
        # create the model
        model = RandomForestClassifier()
    elif MODEL_NAME == "SVM":
        # create the model
        model = svm.SVC()
    elif MODEL_NAME == "KNN":
        # create the model
        model = KNeighborsClassifier()
    elif MODEL_NAME == "MLP":
        # create the model
        model = MLPClassifier()
    else:
        raise Exception("Invalid model name")
    # train the model
    model.fit(train_x, train_y)
    # return the model
    return model


In [33]:
# calculate the metrics
def calculate_metrics(test_y, predicted_y):
    # calculate the metrics
    accuracy = accuracy_score(test_y, predicted_y)
    precision = precision_score(test_y, predicted_y)
    recall = recall_score(test_y, predicted_y)
    f1 = f1_score(test_y, predicted_y,
                #   pos_label=LABEL_OF_POSITIVE_CLASS
                  )
    # return the metrics
    return accuracy, precision, recall, f1

In [34]:

# combine all the steps
def scoring_module(data: pd.DataFrame, NUMBER_OF_ITERATION: int, MODEL_NAME: str, NORMALIZATION: str):
    # create a list to store the metrics
    metrics = []
    # repeat the process NUMBER_OF_ITERATION times
    for i in range(NUMBER_OF_ITERATION):
        # split the data into train and test
        train_x, test_x, train_y, test_y = split_data(data)
        # normalize the data
        train_x, test_x = normalize_data(train_x, test_x, NORMALIZATION)
        # train the model
        model = train_model(train_x, train_y, MODEL_NAME)
        # predict the test data
        predicted_y = model.predict(test_x)
        # calculate the metrics
        accuracy, precision, recall, f1 = calculate_metrics(test_y, predicted_y)
        # store the metrics
        metrics.append([accuracy, precision, recall, f1])
    # return the metrics
    return metrics


In [35]:

# calculate the average of the metrics
def calculate_group_average_metrics(metrics):
    # calculate the average of the metrics
    return np.mean(metrics, axis=0)

In [ ]:
train_v2.head()

## Assign Ranks For Groups and Features

In [65]:
import pandas as pd
import re

def filter_dataframe_by_features(df_columns, feature_list):
    """
    Efficiently filter a DataFrame to include only columns that match the given feature list,
    allowing for extra information in parentheses.
    
    Parameters:
    df (pandas.DataFrame): The input DataFrame
    feature_list (list): List of features to keep
    
    Returns:
    pandas.DataFrame: A new DataFrame containing only the specified features
    """
    # Create a single regex pattern for all features
    pattern = r'^(' + '|'.join(re.escape(feature) for feature in feature_list) + r')(\s*\([^)]*\))?$'
    regex = re.compile(pattern)
    
    # Use vectorized operations to filter columns
    mask = df_columns.str.match(regex)
    columns_to_keep = df_columns[mask]
    
    # Return a new DataFrame with only the specified columns
    return columns_to_keep

# Example usage:
# features = ['A1BG', 'NAT2', 'SERPINA3', 'AAVS1', 'ABCA1', 'ABL1', 'ABO']
# filtered_data = filter_dataframe_by_features(data, features)

## Apply Scoring to each Group

In [66]:
import pandas as pd
from tqdm.notebook import tqdm


# train a new model using each group of features.
# Then, calculate the average of the metrics
def apply_scoring_to_each_group(data, featureList_of_groups):
    # train a new model using each group of features.
    # Then, calculate the average of the metrics
    # create a list to store the metrics
    group_performance_dict = {}
    counter = 0
    for group_name, features in tqdm(list(featureList_of_groups.items())):
        counter += 1
        # give the features as list
        # match the column even if it include extra paranthesis (ADVANCED CODE)
        features = filter_dataframe_by_features(data.columns, features)
        # if the length of the features is 0, then skip
        if len(features) == 0:
            group_performance_dict[group_name] = []
            continue
        # add class to the beginning of each feature
        features.insert(0, 'class')
        data_temp = data[features]
        metrics = []
        # repeat the process NUMBER_OF_ITERATION times
        for i in range(NUMBER_OF_ITERATION):
            # split the data into train and test
            train_x, test_x, train_y, test_y = split_data(data_temp)
            # normalize the data
            train_x, test_x = normalize_data(train_x, test_x, NORMALIZATION)
            # train the model
            model = train_model(train_x, train_y, MODEL_NAME)
            # predict the test data
            predicted_y = model.predict(test_x)
            # calculate the metrics
            accuracy, precision, recall, f1 = calculate_metrics(test_y, predicted_y)
            # store the metrics
            metrics.append([accuracy, precision, recall, f1])
        # get the average of the metrics
        metrics = calculate_group_average_metrics(metrics)
        if counter > 4:
            break

    # return the metrics
    return metrics

In [67]:

from line_profiler import LineProfiler
lp = LineProfiler()
# lp.run("apply_anova_levene_test(train, FILTER_FEATURES_BY_TTEST_TO)")
# lp_wrapper = lp(apply_scoring_to_each_group)
# lp_wrapper(train_v2, featureList_of_groups)

# measure the time it takes to run the "filter_dataframe_by_features" inside the "apply_scoring_to_each_group" function
lp_wrapper = lp(apply_scoring_to_each_group)
lp_wrapper(train_v2, featureList_of_groups)

  0%|          | 0/3929 [00:00<?, ?it/s]

KeyError: 'class'

In [59]:
lp.print_stats()

Timer unit: 1e-07 s

Total time: 13.7655 s
File: C:\Users\Lenovo\AppData\Local\Temp\ipykernel_35116\2098223970.py
Function: apply_scoring_to_each_group at line 7

Line #      Hits         Time  Per Hit   % Time  Line Contents
     7                                           def apply_scoring_to_each_group(data, featureList_of_groups):
     8                                               # train a new model using each group of features.
     9                                               # Then, calculate the average of the metrics
    10                                               # create a list to store the metrics
    11         1          6.0      6.0      0.0      group_performance_dict = {}
    12         1          3.0      3.0      0.0      counter = 0
    13         6     204838.0  34139.7      0.1      for group_name, features in tqdm(list(featureList_of_groups.items())):
    14         6         28.0      4.7      0.0          counter += 1
    15                          

In [55]:
columns = filter_dataframe_by_features(train_v2.columns, ["deneme", "deneme2"])
columns

[]

In [61]:
lp_2 = LineProfiler()
lp_2_wrapper = lp_2(filter_dataframe_by_features)
lp_2_wrapper(train_v2.columns, ["deneme", "deneme2"])
lp_2.print_stats()

Timer unit: 1e-07 s

Total time: 0.0046809 s
File: C:\Users\Lenovo\AppData\Local\Temp\ipykernel_35116\1419679059.py
Function: filter_dataframe_by_features at line 4

Line #      Hits         Time  Per Hit   % Time  Line Contents
     4                                           def filter_dataframe_by_features(df_columns, feature_list):
     5                                               """
     6                                               Filter a DataFrame to include only columns that match the given feature list,
     7                                               allowing for extra information in parentheses.
     8                                               
     9                                               Parameters:
    10                                               df (pandas.DataFrame): The input DataFrame
    11                                               feature_list (list): List of features to keep
    12                                               
    13

In [ ]:
all_group_feature_match_with_metrics = all_group_feature_match_with_metrics_original.reset_index(drop=True)
all_group_feature_match_with_metrics

## Save Group Feature Matches with Metrics

In [95]:
# save all_group_feature_matches to a csv file in the output folder
output_folder = project_folder / "output"
output_folder.mkdir(parents=True, exist_ok=True)
output_file = output_folder / "all_group_feature_matches.csv"
all_group_feature_match_with_metrics.to_csv(output_file, index=False)

In [96]:
# sort the average of the metrics by accuracy
average_metrics_of_groups = average_metrics_of_groups.sort_values(by="accuracy", ascending=False)

In [ ]:
average_metrics_of_groups

### Save Ranked Groups

In [98]:
# save the average of the metrics to a file in the output folder
output_folder = project_folder / "output"
output_folder.mkdir(parents=True, exist_ok=True)
output_file = output_folder / "average_metrics_of_groups.txt"
average_metrics_of_groups.to_csv(output_file, sep="\t")

In [99]:
#! # find in average_metrics index and print it with its metrics and rank 
# name = "Thymic Adenosquamous Carcinoma"
# print(average_metrics_of_groups.index.get_loc(name) + 1)
# print(average_metrics_of_groups.loc[name])

## Remove Lower Scored Groups 

In [100]:
# Take the best performed groups
# Find the associated features to these groups and filter them
def filter_features_by_groups(data, groups_of_features, average_metrics_of_groups, FILTER_BEST_X_GROUPS):
    # get the best performed groups
    best_performed_groups = average_metrics_of_groups.index[:FILTER_BEST_X_GROUPS].to_list()
    # for each group, get associated features and store them in a list
    features_of_best_performed_groups = []
    for group in best_performed_groups:
        features_of_best_performed_groups += [feature for feature, groups in groups_of_features.items() if group in groups]
    # remove the duplicate features
    print("Number of features before removing duplicates: ", len(features_of_best_performed_groups))
    features_of_best_performed_groups = list(set(features_of_best_performed_groups))
    print("Duplicate features are removed. Number of features: ", len(features_of_best_performed_groups))
    # filter the data by the features
    data = data[["class"] + features_of_best_performed_groups]
    # return the filtered data and features_of_best_performed_groups
    return data, features_of_best_performed_groups

In [ ]:
# filter the data by the features_of_best_performed_groups
train_v3, features_of_best_performed_groups  = filter_features_by_groups(train_v2, featureList_of_groups, average_metrics_of_groups, FILTER_BEST_X_GROUPS)
test_v3 = test_v2[["class"] + features_of_best_performed_groups]

In [ ]:
features_of_best_performed_groups

In [ ]:
train_v3.head(10)

## Modeling

In [104]:
def calculate_metrics(test_y, predicted_y):
    # calculate the metrics
    accuracy = accuracy_score(test_y, predicted_y)
    precision = precision_score(test_y, predicted_y)
    recall = recall_score(test_y, predicted_y)
    f1 = f1_score(test_y, predicted_y)
    # return the metrics
    return accuracy, precision, recall, f1

# take the final data, train a model with it and calculate the metrics using test data
def final_scoring_module(train, test, MODEL_NAME):
    # split the data into labels and features
    train_x = train.drop("class", axis=1)
    train_y = train["class"]
    test_x = test.drop("class", axis=1)
    test_y = test["class"]
    # train the model
    model = train_model(train_x, train_y, MODEL_NAME)
    try:
        # predict the probability of test data
        predicted_y_proba = model.predict_proba(test_x)
        print(predicted_y_proba)
        # get the probability of the positive class
        predicted_y_proba = predicted_y_proba[:, 1]
    except:
        print("The probability of test data cannot be predicted. The model does not have the attribute 'predict_proba'")
        # predict the test data
        predicted_y_proba = model.predict(test_x)
    # convert the predicted_y_proba to binary
    predicted_y = np.where(predicted_y_proba > 0.5, 1, 0)
    # calculate the metrics
    accuracy, precision, recall, f1 = calculate_metrics(test_y, predicted_y)
    # return the metrics
    return accuracy, precision, recall, f1, predicted_y_proba

In [ ]:
# calculate the metrics for the final data
accuracy, precision, recall, f1, predicted_y_proba = final_scoring_module(train_v3, test_v3, MODEL_NAME)
print("Accuracy: ", accuracy)
print("Precision: ", precision)
print("Recall: ", recall)
print("F1: ", f1)

### Draw a ROC Curve

In [ ]:
# import lib for precision, recall and roc
import matplotlib.pyplot as plt
from sklearn.metrics import roc_curve


def calculate_roc_values(test_y, predicted_y_proba):
    # calculate the fpr and tpr
    fpr, tpr, thresholds = roc_curve(test_y, predicted_y_proba)
    # calculate the auc manually
    auc_value = np.trapz(tpr, fpr)
    print("AUC: ", auc_value)
    # return the fpr, tpr and auc
    return fpr, tpr, auc_value

def calculate_tpr_fpr(test_y, predicted_y_proba):
    thresholds = np.linspace(0, 1, num=100)
    # calculate the precision and recall manually
    precision = []
    recall = []
    tpr, fpr = [], []
    for threshold in thresholds:
        predicted_y = (predicted_y_proba >= threshold).astype(int)
        tp = np.sum((predicted_y == 1) & (test_y == 1))
        fp = np.sum((predicted_y == 1) & (test_y == 0))
        fn = np.sum((predicted_y == 0) & (test_y == 1))
        tn = np.sum((predicted_y == 0) & (test_y == 0))
        print("tp: ", tp, "fp: ", fp, "fn: ", fn, "tn: ", tn)
        tpr.append(tp / (tp + fn))
        fpr.append(fp / (fp + tn))
        precision.append(tp / (tp + fp))
        recall.append(tp / (tp + fn))
    # calculate the auc
    auc_value = np.trapz(precision, recall)
    # return the precision, recall and auc
    return tpr, fpr, auc_value, thresholds


# calculate the roc values
tpr, fpr, auc_value = calculate_roc_values(test_v3['class'], predicted_y_proba)
# calculate the tpr, fpr, auc and thresholds
# tpr, fpr, auc_value, thresholds = calculate_tpr_fpr(test_v3['class'], predicted_y)

# plot the roc curve
# plt.plot(fpr, tpr, color='darkorange', lw=2, label='ROC curve (area = %0.2f)' % auc_value)
plt.plot(tpr, fpr, color='darkorange', lw=2, label='ROC curve (area = %0.2f)' % auc_value)
plt.plot([0, 1], [0, 1], color='navy', lw=2, linestyle='--')
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive Rate')
plt.title('ROC Curve of ' + MODEL_NAME)
plt.legend(loc="lower right")
# make the text bigger
plt.rcParams.update({'font.size': 15})
plt.show()

# draw the precision recall curve
# plt.plot(recall, precision, color='darkorange', lw=2, label='PR curve (area = %0.2f)' % auc_value)
# plt.xlabel('Recall')
# plt.ylabel('Precision')
# plt.title('Precision Recall Curve')
# plt.legend(loc="lower right")
# plt.show()

In [ ]:
fpr, tpr, thresholds

# Save Results

## Apply Robust Rank Aggregation to Groups

In [ ]:
# apply borda rank aggregation for each group
import ranky as rk

def apply_borda_rank_aggregation_for_each_group(all_group_feature_match_with_metrics):
    # get the groups
    groups = all_group_feature_match_with_metrics["group"].unique()
    # create a dataframe to store the aggregated ranks
    aggregated_ranks = pd.DataFrame(columns=["rank", "group"])
    # for each group
    for group in groups:
        # get the features of the group
        features_of_group = all_group_feature_match_with_metrics[all_group_feature_match_with_metrics["group"] == group]
        # get the ranks with the columns "f1", "recall", "precision", "accuracy" and turn into list
        ranks = features_of_group[["f1", "recall", "precision", "accuracy"]].values.tolist()
        # apply borda rank aggregation
        aggregated_ranks_of_group = rk.borda(ranks)
        # store the aggregated ranks
        aggregated_ranks_of_group["group"] = group
        aggregated_ranks = aggregated_ranks.append(aggregated_ranks_of_group)
    # return the aggregated ranks
    return aggregated_ranks

In [ ]:
# apply borda rank aggregation for each group
aggregated_ranks = apply_borda_rank_aggregation_for_each_group(all_group_feature_match_with_metrics)

In [ ]:
import pandas as pd
from ranky import FullListRankAggregator

def rank_aggregation(df):
    # Assuming your data is in a pandas DataFrame named 'df'
    # with columns 'Iteration' and 'feature_group'

    # Group data by 'Iteration'
    grouped_data = df.groupby('Iteration')['feature_group'].apply(list).tolist()

    # Count unique genes across all data subsets
    tot_genes = len(set(item for sublist in grouped_data for item in sublist))

    # Convert string ranks to numerical ranks (optional, only if necessary)
    # If ranks are already numerical, skip this step
    for idx, group in enumerate(grouped_data):
        try:
            # Assuming ranks are integers
            grouped_data[idx] = [int(rank) for rank in group]
        except ValueError:
            # Handle non-integer ranks if necessary (e.g., using ranky.ranks_from_strings)
            print("ValueError")
            
    # Create a ranky FullListRankAggregator object
    ranker = FullListRankAggregator()

    # Aggregate ranks (replace 'borda' with another method if desired)
    aggregated_ranks = ranker.aggregate_ranks(grouped_data, method='borda')

    # Print or handle aggregated ranks as needed
    print(aggregated_ranks)  # Or write to a CSV file, database, etc.

# Main Function